In [9]:
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import BaggingClassifier
from sklearn.ensemble import IsolationForest
from sklearn.metrics import accuracy_score, f1_score
from sklearn import tree
import matplotlib.pyplot as plt
import math
import numpy as np

In [78]:
train = pd.read_csv("train.csv")
train_drop = train.drop(['PassengerId', 'Name', 'Ticket', 'Cabin'], axis = 1)

In [79]:
age_avg = round(train_drop['Age'].mean())
values  = {"Age" : age_avg}
train_drop = train_drop.fillna(value=values) 
train_drop_ = train_drop.dropna()

In [80]:
sex_map = {"male":0, "female":1}
embark_map = {"S":0, "C":1,"Q":2}

train_drop_map = train_drop_.copy()
train_drop_map['Sex'] = train_drop_map['Sex'].map(sex_map)
train_drop_map['Embarked'] = train_drop_map['Embarked'].map(embark_map)

train_drop_map

Survived  Pclass  Sex   Age  SibSp  Parch     Fare  Embarked
0           0       3    0  22.0      1      0   7.2500         0
1           1       1    1  38.0      1      0  71.2833         1
2           1       3    1  26.0      0      0   7.9250         0
3           1       1    1  35.0      1      0  53.1000         0
4           0       3    0  35.0      0      0   8.0500         0
..        ...     ...  ...   ...    ...    ...      ...       ...
886         0       2    0  27.0      0      0  13.0000         0
887         1       1    1  19.0      0      0  30.0000         0
888         0       3    1  30.0      1      2  23.4500         0
889         1       1    0  26.0      0      0  30.0000         1
890         0       3    0  32.0      0      0   7.7500         2

[889 rows x 8 columns]

In [81]:
quartiles = np.percentile(train_drop_map['Age'], [25, 50, 75])
mu = quartiles[1]
sig = 0.74 * (quartiles[2] - quartiles[0])

train_rm_outlier = train_drop_map.query(' (Age > @mu - 5*@sig) & (Age < @mu + 5*@sig)')


In [82]:
train_scale = train_rm_outlier.copy()
label = train_scale.iloc[:, 0].values
feature = train_scale.iloc[:, 1:7].values

train_label, test_label, train_feature, test_feature = train_test_split(label, feature, test_size = 0.3, random_state = 42)



In [83]:
print("\t", end = "")
print("[Train acc.]", end = "")
print("[Train F1s.]", end = "")
print("[Test acc. ]", end = "")
print("[Test F1s. ]")
k_range = range(1,6)
scores = []
for k in k_range:
  knn = KNeighborsClassifier(n_neighbors=k)
  knn.fit(train_feature, train_label)
  train_pred = knn.predict(train_feature)
  train_accuracy = accuracy_score(train_label, train_pred)
  train_f1 = f1_score(train_label, train_pred)

  test_pred = knn.predict(test_feature)
  test_accuracy = accuracy_score(test_label, test_pred)
  test_f1 = f1_score(test_label, test_pred)
  print("[k : %d]" % k, end = " ")
  print("|  %.3f  |" % (train_accuracy * 100), end ="")
  print("|  %.3f  |" %(train_f1 * 100), end ="")
  print("|  %.3f  |" % (test_accuracy * 100), end ="")
  print("|  %.3f  |" % (test_f1 * 100))


	[Train acc.][Train F1s.][Test acc. ][Test F1s. ]
[k : 1] |  98.068  ||  97.479  ||  68.539  ||  54.839  |
[k : 2] |  84.219  ||  74.211  ||  69.663  ||  43.357  |
[k : 3] |  83.253  ||  77.966  ||  69.288  ||  55.435  |
[k : 4] |  79.871  ||  70.309  ||  68.539  ||  48.148  |
[k : 5] |  80.193  ||  73.774  ||  71.536  ||  58.242  |


In [84]:
print("\t", end = "     ")
print("[Train acc.]", end = "")
print("[Train F1s.]", end = "")
print("[Test acc. ]", end = "")
print("[Test F1s. ]")
for iter in [0, 20, 40, 60, 80, 100]:
  log_reg = LogisticRegression(max_iter=iter)
  log_reg.fit(train_feature, train_label)
  train_predict = log_reg.predict(train_feature)
  test_predict = log_reg.predict(test_feature)
  if iter == 100:
    print("[#iter : %d]" % iter, end = "")
    print("|  %.3f  |" %(accuracy_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(accuracy_score(test_predict, test_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(test_predict, test_label)*100))
  elif iter == 0:
    print("[#iter : %d  ]" % iter, end = "")
    print("|  %.3f  |" %(accuracy_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(accuracy_score(test_predict, test_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(test_predict, test_label)*100))
  else:
    print("[#iter : %d ]" % iter, end = "")
    print("|  %.3f  |" %(accuracy_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(train_predict, train_label)*100), end ="")
    print("|  %.3f  |" %(accuracy_score(test_predict, test_label)*100), end ="")
    print("|  %.3f  |" %(f1_score(test_predict, test_label)*100)) 

	     [Train acc.][Train F1s.][Test acc. ][Test F1s. ]
[#iter : 0  ]|  66.667  ||  47.059  ||  69.288  ||  48.101  |
[#iter : 20 ]|  79.871  ||  71.910  ||  80.524  ||  74.000  |
[#iter : 40 ]|  80.193  ||  72.483  ||  80.150  ||  72.539  |
[#iter : 60 ]|  79.388  ||  71.681  ||  80.899  ||  74.627  |
[#iter : 80 ]|  79.388  ||  72.052  ||  80.899  ||  74.627  |
[#iter : 100]|  78.744  ||  71.429  ||  80.899  ||  74.877  |


/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)
/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:940: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression


In [67]:
print("\t", end = "")
print("[Train acc.]", end = "")
print("[Train F1s.]", end = "")
print("[Test acc. ]", end = "")
print("[Test F1s. ]")
for c in range(1,6):
  log_reg = LogisticRegression(max_iter=100, C=c)
  log_reg.fit(train_feature, train_label)
  train_predict = log_reg.predict(train_feature)
  test_predict = log_reg.predict(test_feature)
  print("[c : %d]" % c, end = " ")
  print("|  %.3f  |" %(accuracy_score(train_predict, train_label)*100), end ="")
  print("|  %.3f  |" %(f1_score(train_predict, train_label)*100), end ="")
  print("|  %.3f  |" %(accuracy_score(test_predict, test_label)*100), end ="")
  print("|  %.3f  |" %(f1_score(test_predict, test_label)*100))



	[Train acc.][Train F1s.][Test acc. ][Test F1s. ]
[c : 1] |  78.744  ||  71.429  ||  80.899  ||  74.877  |
[c : 2] |  78.905  ||  71.584  ||  80.524  ||  74.510  |
[c : 3] |  78.905  ||  71.584  ||  80.524  ||  74.510  |
[c : 4] |  78.905  ||  71.584  ||  80.524  ||  74.510  |
[c : 5] |  78.905  ||  71.584  ||  80.524  ||  74.510  |


In [27]:
DT_model = DecisionTreeClassifier(criterion='entropy')
DT_model.fit(train_feature, train_label)
train_predict = DT_model.predict(train_feature)
test_predict = DT_model.predict(test_feature)

print("Train data set accuracy : %.3f" %(accuracy_score(train_predict, train_label)*100))
print("Train data set F1_Score : %.3f" %(f1_score(train_predict, train_label)*100))
print("Test data set accuracy : %.3f" %(accuracy_score(test_predict, test_label)*100))
print("Test data set F1_Score : %.3f" %(f1_score(test_predict, test_label)*100))

Train data set accuracy : 98.068
Train data set F1_Score : 97.436
Test data set accuracy : 78.652
Test data set F1_Score : 70.157


In [20]:
feature_name = []
for i in train_feature:
  feature_name.append(i)

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 10), dpi=1800)

tree.plot_tree(DT_model,
               feature_names=feature_name,
               class_names="Survived",
               filled=True)

fig.savefig('Decision_Tree.png')

In [75]:
print("\t", end = "  ")
print("[Train acc.]", end = "")
print("[Train F1s.]", end = "")
print("[Test acc. ]", end = "")
print("[Test F1s. ]")
for bag in range(1,6):
  BT_model = BaggingClassifier(base_estimator=DecisionTreeClassifier(), n_estimators= bag)
  BT_model.fit(train_feature, train_label)
  train_predict = BT_model.predict(train_feature)
  test_predict = BT_model.predict(test_feature)
  print("[bag : %d]" % bag, end = " ")
  print("|  %.3f  |" %(accuracy_score(train_predict, train_label)*100), end ="")
  print("|  %.3f  |" %(f1_score(train_predict, train_label)*100), end ="")
  print("|  %.3f  |" %(accuracy_score(test_predict, test_label)*100), end ="")
  print("|  %.3f  |" %(f1_score(test_predict, test_label)*100))


	  [Train acc.][Train F1s.][Test acc. ][Test F1s. ]
[bag : 1] |  92.271  ||  89.916  ||  76.030  ||  68.317  |
[bag : 2] |  93.237  ||  90.583  ||  79.026  ||  69.892  |
[bag : 3] |  95.491  ||  94.093  ||  77.903  ||  70.647  |
[bag : 4] |  94.042  ||  91.868  ||  79.401  ||  72.081  |
[bag : 5] |  95.813  ||  94.538  ||  82.397  ||  76.142  |
